In [1]:
import os
import time
from datetime import datetime

from utils import *
from model.MLP import *

import numpy as np
import nibabel as nib
import matplotlib.pyplot as plt
import pandas as pd
from scipy.stats import pearsonr


import torch

import torch.nn as nn
from torch.utils.data import TensorDataset, DataLoader
from torch.utils.tensorboard import SummaryWriter

from torchsummary import summary


os.environ["CUDA_VISIBLE_DEVICES"] = ""
device = torch.device('cuda' if torch.cuda.is_available() else "cpu")
print(device)
print(torch.cuda.device_count())

input_sizes = {'15':105,
                '25':300,
                '50':1225,
                '100':4950,
                '200':19900,
                '300':44850
                }




cpu
0


In [3]:
df = pd.read_csv(os.path.join('./data/netmats/ICA300/connectivity_ICA300.csv'))
df

1         2       3        4       5        6        7       8  \
0      7.49720  23.35000  78.054  -4.9579  43.429  60.4470  41.4040 -7.5742   
1     -4.99950   4.73090  54.711  -6.9007  13.804  30.3770  26.1270 -2.1377   
2      9.40280   5.24820  99.701 -12.2550  30.410  67.0210  49.9930  1.2277   
3    -28.31500 -13.18600  59.763 -24.9000  16.699  44.6980  34.0170 -8.2790   
4     -0.14134   8.04310  63.203  -2.1901  24.454  46.9130  31.4790  5.5834   
...        ...       ...     ...      ...     ...      ...      ...     ...   
998   -0.85452   3.24290  60.144  -6.1011  10.891  55.0160  64.7880 -9.6518   
999    3.42850  10.47600  92.195 -12.6510  35.189  47.2660  52.4960  7.3938   
1000   4.76000  16.95700  20.941  14.9970  27.368   7.6914   8.8762  1.4107   
1001   5.93070  -0.43158  86.431 -17.4260  27.843  64.6700  66.5200 -4.5230   
1002  -8.51760   3.63140  46.417  -6.0625  28.845  23.8540  40.2890  7.0224   

             9         10  ...     88798    88799    89097    89098     89099  \
0     17.58300  -2.662400  ... -0.658430 -3.31760  2.79060  1.33920  2.231700   
1     18.45000 -14.857000  ... -0.780040 -1.70270 -1.00820  0.36915 -0.664390   
2      1.40360  -0.461260  ... -3.392200 -0.56904  3.66550  1.26210  2.101300   
3      5.16900   0.089982  ...  0.124290 -0.36566 -0.94756 -0.63533  1.234200   
4      2.11680   9.282800  ... -1.795900  3.17070  1.39460  0.79006  0.775760   
...        ...        ...  ...       ...      ...      ...      ...       ...   
998    4.97660 -12.543000  ...  1.257800  2.77780  0.22414 -0.47279  2.964200   
999    0.57836   4.123800  ...  0.643660 -2.93160  0.24456  3.25640  1.213900   
1000  -1.37530  -8.494300  ... -1.795200 -1.09860  0.55332 -0.11358 -1.547500   
1001  -5.20640  15.786000  ...  0.019416 -2.32110  0.79256  0.14387 -0.053458   
1002  -2.15310   9.071000  ... -0.015315  0.26386 -0.75828 -2.38870  0.922310   

        89398    89399   89699  sex  fluid_intelligence  
0     1.51680 -0.28532  4.6379    0                20.0  
1     1.45510 -0.76610  4.5984    1                17.0  
2     0.78259  1.19860  4.4317    0                 7.0  
3     1.27270  0.46160  6.1709    0                23.0  
4     0.17996 -2.84420  2.9442    1                11.0  
...       ...      ...     ...  ...                 ...  
998  -0.26596 -1.32200  7.5611    1                21.0  
999  -0.68257  1.07780  4.9371    0                14.0  
1000 -0.76885  1.31420  6.4576    1                21.0  
1001 -0.63690 -1.50930  5.8259    0                20.0  
1002  1.72560 -1.57620  4.3008    1                20.0  

[1003 rows x 44852 columns]

In [2]:
nbr_components= 50
data_path = '/home/sd20/workspace/data/HCP/'


loader = dataLoaderICA(data_path = './data/netmats',
                        nbr_components = nbr_components,
                        batch_size = 32,
                        num_workers = 8,
                        label ='fluid_intelligence',)

dataloaders = loader.getDataLoaders()

shape X train (799, 1225) , y train (799,)
shape X val (200, 1225) , y val (200,)


In [3]:
for i, data in enumerate(dataloaders['train']):
    print(i)
    print(data[0].shape, data[1].shape)
    break


0
torch.Size([32, 1225]) torch.Size([32])


In [4]:
net = MLP(input_size=300,
          hidden_size=[16],
          dropout=0.5)

net

MLP(
  (fc_layers): ModuleDict(
    (fc_layer_0): Linear(in_features=300, out_features=16, bias=False)
  )
  (fc_class): Linear(in_features=16, out_features=1, bias=False)
  (dropout): Dropout(p=0.5, inplace=False)
  (relu): ReLU()
)

#### Optimiser, Loss and Training parameters

FLUID INTELLIGENCE

In [5]:
nbr_components = 50

input_size = input_sizes[str(nbr_components)]
hidden_size = [16,16]
dropout = 0.5
batch_size = 64


n_epochs = 1000
lr = 1e-5

In [6]:
# loaders
loader = dataLoaderICA(data_path = './data/netmats',
                        nbr_components = nbr_components,
                        batch_size = batch_size,
                        num_workers = 0,
                        label ='fluid_intelligence',)


dataloaders = loader.getDataLoaders()

# network
net = MLP(input_size,
          hidden_size,
          dropout,)

#loss
loss = nn.MSELoss()

#optimiser
optimiser = torch.optim.Adam(net.parameters(), lr=lr)

#lr scheduler

#metrics to store during training
metrics = {'loss_train': [], 'loss_valid': [], 
           'acc_train': [], 'acc_valid':[]}

shape X train (799, 1225) , y train (799,)
shape X val (200, 1225) , y val (200,)


In [7]:
net

MLP(
  (fc_layers): ModuleDict(
    (fc_layer_0): Linear(in_features=1225, out_features=16, bias=False)
    (fc_layer_1): Linear(in_features=16, out_features=16, bias=False)
  )
  (fc_class): Linear(in_features=16, out_features=1, bias=False)
  (dropout): Dropout(p=0.5, inplace=False)
  (relu): ReLU()
)

In [34]:
path = '/home/sd20/workspace/spatio-temporal-fmri-analysis'
date = datetime.today().strftime('%Y-%m-%d')
print(date)

# folder date
folder_to_save_model = os.path.join(path,'logs', date)
try:
    os.mkdir(folder_to_save_model)
    print('Creating folder: {}'.format(folder_to_save_model))
except OSError:
    print('folder already exist: {}'.format(folder_to_save_model))

date = datetime.today().strftime('%H:%M:%S')
print(date)

# folder ICA
folder_to_save_model = os.path.join(folder_to_save_model,'fluid/ICA_{}'.format(nbr_components))

# folder time
folder_to_save_model = os.path.join(folder_to_save_model,date)
try:
    os.mkdir(folder_to_save_model)
    print('Creating folder: {}'.format(folder_to_save_model))
except OSError:
    print('folder already exist: {}'.format(folder_to_save_model))




# tensorboard 
writer = SummaryWriter(log_dir=folder_to_save_model)

2021-06-15
folder already exist: /home/sd20/workspace/spatio-temporal-fmri-analysis/logs/2021-06-15
12:35:25
Creating folder: /home/sd20/workspace/spatio-temporal-fmri-analysis/logs/2021-06-15/fluid/ICA_50/12:35:25


In [35]:
best_train_epoch = 0.0
best_val_epoch = 0.0

for epoch in range(0, n_epochs):
    print('#'*50)

    # Print learning rate for each epoch -- good for when you have a LR scheduler
    #scheduler.step()
    #lr = optim.param_groups[0]['lr']
    #print('lr = %.7f' % lr)

    # Save time to calculate how long it took
    start_time = time.time()

    # Append emtpy list so that each epoch has a list of values
    for key_ in metrics.keys():
        metrics[key_].append([])

    predictions_val = []
    gt_val =[]
    epoch_acc_val = []
    epoch_acc_train = []


    # Go through each phase TRAIN/VALID
    #####################################################  
    for phase in ['train','valid']:

        correlation = []
        total_correct = 0.0
        total_size = 0.0

        # Go through each data point in either train or validation
        #####################################################  
        for i, (inputs, labels) in enumerate(dataloaders[phase]):
            
            # Calculates step
            length_dataloader = len(dataloaders[phase])
            step = epoch * length_dataloader + i + 1

            # Fetch batch of data
            ##################################################
            # Image data
            inputs = inputs.to(device)
            
            # Label data
            lab_gt = labels.to(device)
            

            # TRAIN
            ##################################################
            if phase == 'train':

                optimiser.zero_grad()

                outputs =  net(inputs).squeeze()  

                current_loss =  loss(outputs,labels) 
                print(current_loss)

                #####
                metrics['loss_train'][-1].append(current_loss.item())
                writer.add_scalar('loss/train', current_loss.item(), epoch*length_dataloader+i)

                #####
                current_loss.backward() 

                optimiser.step()
        
            if phase == 'valid':

                net.eval()

                with torch.no_grad():

                    outputs_val = net(inputs).squeeze()
                    print('')
                    print(outputs_val)
                    print(lab_gt)
                    print(pearsonr(outputs_val,lab_gt))
                    correlation.append(pearsonr(outputs_val,lab_gt)[0])
                    print('')

                    current_loss = loss(outputs_val, lab_gt)

                    metrics['loss_valid'][-1].append(current_loss.item())
                    writer.add_scalar('loss/val', current_loss.item(), epoch*length_dataloader+i)

        if phase =='valid':

            writer.add_scalar('correlation/val', np.mean(correlation), epoch*length_dataloader+i)

   
        print('')
        

##################################################
tensor(260.2248, grad_fn=<MseLossBackward>)
tensor(266.1946, grad_fn=<MseLossBackward>)
tensor(274.6830, grad_fn=<MseLossBackward>)
tensor(259.7208, grad_fn=<MseLossBackward>)
tensor(237.4679, grad_fn=<MseLossBackward>)
tensor(254.7448, grad_fn=<MseLossBackward>)
tensor(264.2440, grad_fn=<MseLossBackward>)
tensor(255.8138, grad_fn=<MseLossBackward>)
tensor(243.3190, grad_fn=<MseLossBackward>)
tensor(259.8511, grad_fn=<MseLossBackward>)
tensor(268.4970, grad_fn=<MseLossBackward>)
tensor(249.5258, grad_fn=<MseLossBackward>)
tensor(208.5392, grad_fn=<MseLossBackward>)


tensor([3.0668, 1.9888, 1.7564, 2.6119, 1.9124, 3.1491, 2.0262, 3.2079, 2.2978,
        2.0876, 2.1497, 0.3807, 4.1018, 2.8120, 2.5220, 2.2595, 2.0690, 1.8671,
        2.5898, 1.9412, 3.2697, 0.7031, 2.4439, 1.2967, 3.9893, 3.3055, 3.4355,
        3.7384, 2.4750, 2.3388, 2.6231, 1.6269, 3.6071, 2.8915, 4.6938, 2.5859,
        1.7617, 1.1217, 3.2631, 1.1337, 1.9820, 2.0028,